In [1]:
!pip install matplotlib
!pip install sklearn
!pip install tqdm
!pip install torch
!pip install torchvision
!pip install pandas
!pip install transformers

You should consider upgrading via the '/home/alhiris/.pyenv/versions/3.9.9/bin/python3.9 -m pip install --upgrade pip' command.
Using legacy 'setup.py install' for sklearn, since package 'wheel' is not installed.
    Running setup.py install for sklearn ... done
You should consider upgrading via the '/home/alhiris/.pyenv/versions/3.9.9/bin/python3.9 -m pip install --upgrade pip' command.
You should consider upgrading via the '/home/alhiris/.pyenv/versions/3.9.9/bin/python3.9 -m pip install --upgrade pip' command.
You should consider upgrading via the '/home/alhiris/.pyenv/versions/3.9.9/bin/python3.9 -m pip install --upgrade pip' command.
You should consider upgrading via the '/home/alhiris/.pyenv/versions/3.9.9/bin/python3.9 -m pip install --upgrade pip' command.
You should consider upgrading via the '/home/alhiris/.pyenv/versions/3.9.9/bin/python3.9 -m pip install --upgrade pip' command.
You should consider upgrading via the '/home/alhiris/.pyenv/versions/3.9.9/bin/python3.9 -m pip i

In [2]:
!nvidia-smi

Wed May 25 15:58:26 2022       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 510.73.05    Driver Version: 510.73.05    CUDA Version: 11.6     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  NVIDIA GeForce ...  Off  | 00000000:01:00.0 Off |                  N/A |
| N/A   44C    P8     6W /  N/A |      5MiB /  4096MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

In [1]:
import matplotlib.patches as patches
import matplotlib.pyplot as plt
from sklearn.metrics import accuracy_score
from tqdm import tqdm
import json
import torch as t
import torch
import torch.nn as nn
from PIL import Image
import numpy as np
from torch.utils.data import Dataset, DataLoader, random_split
from torchvision.transforms.functional import to_tensor, normalize
import torchvision.transforms as transforms
import random
import torchvision.models as models
import os
from torchvision.transforms.functional import to_tensor
import pandas as pd

random_seed_run = int(np.random.rand() * 10000)
counter_dirs = 0
seed = 42
np.random.seed(seed)
np.random.RandomState(seed)
random.seed(seed)
torch.manual_seed(seed)
torch.use_deterministic_algorithms(False)

EPOCHS = 10
NUM_LAYERS_FROZEN = 10
lr = 2e-4
DATASET_SIZE = 1500
multitask_lr = 2e-5
C_constant = 100
for base, dirs, files in os.walk("./reports/visual_transformer_simples/"):
    for directory in dirs:
        counter_dirs += 1

data_saved_path = "./reports/visual_transformer_simple/run" + str(counter_dirs) + '_' + str(random_seed_run)
model_save_path = "./models/visual_transformer_simple/run" + str(counter_dirs) + '_'+ str(random_seed_run)
try:
    os.makedirs(data_saved_path)
    os.makedirs(model_save_path)
except:
    print("Directory already exists")

# current_model_path = 'model'
# save_path_model = os.path.join(data_saved_path, current_model_path)


In [2]:
class RoadsignDataset(Dataset):
  def __init__(self, roadsign_root, roadsign_annot, roadsign_imgs, roadsign_temp, feature_extractor, img_size=(224, 224), dataset_size=1500, use_random_template=True, img_type="png"):
    """
    Args:
        dataset_lines (array): array of strings of form "{image_path}|{rectangle_coordinates}".
        width (int): target image width.
        height (int): target image height.
    """
    self.roadsign_root = roadsign_root
    self.roadsign_annot = roadsign_annot
    self.roadsign_imgs = roadsign_imgs
    self.feature_extractor = feature_extractor
    self.img_size = img_size
    self.use_random_template = use_random_template
    self.img_type = img_type
    self.dataset_size=dataset_size

    self.roadsign_annot_file = os.path.join(roadsign_root, roadsign_annot)
    self.roadsign_imgs_dir = os.path.join(roadsign_root, roadsign_imgs)
    self.roadsign_temp_dir = os.path.join(roadsign_root, roadsign_temp)
    
    with open(self.roadsign_annot_file) as infile:
        self.annot_data = json.load(infile)
    self.all_annot_types = self.annot_data['types']
    self.all_annotations = self.annot_data['imgs']

    self.init_dataset()

  def init_dataset(self):
    self.annotations_types = []
    for type in self.all_annot_types:
        full_path = os.path.join(self.roadsign_temp_dir, type + "." + self.img_type)
        if os.path.exists(full_path):
            self.annotations_types.append(type)
    print(self.annotations_types)
    self.annotations_to_id = {ann: idx for idx, ann in enumerate(self.annotations_types)}
    self.id_to_annotations = {idx: ann for ann, idx in self.annotations_to_id.items()}
    print(self.annotations_to_id)
    self.annotations = {}
    current_id = 0
    for key, item in self.all_annotations.items():
        annot_list = [data['category'] for data in item['objects']]
        if len(annot_list) != len(set(annot_list)):
            continue
        for annot_data in item['objects']:
            if annot_data['category'] in self.annotations_types:
                self.annotations[current_id] = {
                    'path': item['path'].split("/")[1],
                    'id': current_id,
                    'object': annot_data
                }
                current_id += 1
    print(len(self.annotations))
    with open(os.path.join(self.roadsign_root, 'new_' + self.roadsign_annot), 'w') as outfile:
        json.dump({
        'types': self.annotations_types,
        'imgs': self.annotations
    }, outfile)
    if self.dataset_size == -1:
        limit_size = self.annotations
    else:
        limit_size = {key: item for key, item in self.annotations.items() if key < self.dataset_size}
    self.annotations = limit_size

  def __len__(self):
    return len(self.annotations)

  def __getitem__(self, idx):
    ok = True
    data = self.annotations[idx]
    img_path = os.path.join(self.roadsign_imgs_dir, data['path'])
    
    use_other_template = np.random.rand()
    annotation = data['object']
    template_used = annotation['category']
    if use_other_template > 0.5 and self.use_random_template:
        use_other_template = 1
        new_id = np.random.randint(len(self.annotations_types))
        while self.annotations_to_id[template_used] == new_id:
            new_id = np.random.randint(len(self.annotations_types))
        template_used = self.id_to_annotations[new_id]
        
    annotation_id = self.annotations_to_id[template_used]
    template_path = os.path.join(self.roadsign_temp_dir, template_used + "." + self.img_type)
    
    img = Image.open(img_path)
    temp = Image.open(template_path)
    if temp.mode == 'RGBA':
        temp = temp.convert('RGB')

    
    original_width, original_height = img.size
    similarity = -1 if use_other_template == 1 else 1

    img = img.resize(self.img_size)
    img = np.array(img)
    temp = temp.resize(self.img_size)
    temp = np.array(temp)

    # if len(img.shape) == 2:
    #   img = np.expand_dims(img, axis=2)
    #   img = np.repeat(img, 3, axis=2)
    # if len(temp.shape) == 2:
    #   temp = np.expand_dims(temp, axis=2)
    #   temp = np.repeat(temp, 3, axis=2)

    img = to_tensor(img)
    temp = to_tensor(temp)

    # temp = to_tensor(temp)
    # transform = transforms.Compose([
    #     transforms.RandomHorizontalFlip(),
    #     transforms.RandomVerticalFlip()
    #     # transforms.ToTensor()
    # ])
    # if random.random() < 0.5:
    # img = transform(img)
    # else:
    #     img = to_tensor(img)

    
    
    bbox = annotation['bbox'] 

    xmin = bbox['xmin']
    xmax = bbox['xmax']
    ymin = bbox['ymin']
    ymax = bbox['ymax']

    # x1 = x1 / original_width * self.img_size[0]
    # x2 = x2 / original_width * self.img_size[0]
    # y1 = y1 / original_height * self.img_size[1]
    # y2 = y2 / original_height * self.img_size[1]
    xmin = xmin / original_width
    xmax = xmax / original_width
    ymin = ymin / original_height
    ymax = ymax / original_height

    coordinates = np.array([xmin, ymin, xmax, ymax])
    coordinates = coordinates.astype(np.float32)
    
    if ok == False:
        processed_imgs = self.feature_extractor(img, return_tensors='pt')
        processed_temps = self.feature_extractor(temp, return_tensors='pt')

        return np.array(processed_imgs['pixel_values']).squeeze(), np.array(processed_temps['pixel_values']).squeeze(), similarity, coordinates
    return img, temp, similarity, coordinates


In [3]:
from IPython.display import clear_output
import time
from transformers import ViTFeatureExtractor

feature_extractor = ViTFeatureExtractor.from_pretrained('google/vit-base-patch16-384')

roadsign_root = "./data/data-roadsign"
roadsign_anno_train = "annotations_all.json"
roadsign_imgs_train = "images"
roadsign_temp_train = "marks"

# coco_anno_valid = os.path.join(coco_root, "data/valid/_annotations.coco.json")
# coco_imgs_valid = os.path.join(coco_root, "data/valid")

batch_train = 6
batch_valid = 1

dataset = RoadsignDataset(roadsign_root, roadsign_anno_train, roadsign_imgs_train, roadsign_temp_train, feature_extractor, dataset_size=DATASET_SIZE, use_random_template=False, img_size=(384, 384))
train_size = int(DATASET_SIZE * 0.8)
valid_size = DATASET_SIZE - train_size
train_dataset, valid_dataset = random_split(dataset, [train_size, valid_size])
train_dataloader = DataLoader(train_dataset, batch_size=batch_train, shuffle=True, num_workers=1)
valid_dataloader = DataLoader(valid_dataset, batch_size=batch_valid, shuffle=False, num_workers=1)

see_examples = 5
fig = plt.figure(figsize=(15, 7*see_examples))
for i, (imgs, temp, similarity, coordinates) in enumerate(train_dataloader):
    clear_output(wait=True)
    imgs = np.transpose(imgs, (0, 2, 3, 1))
    temp = np.transpose(temp, (0, 2, 3, 1))
    fig.add_subplot(see_examples, 2, i * 2 + 1)
    plt.title(similarity[0])
    plt.axis('off')
    plt.imshow(temp[0])
   
    fig.add_subplot(see_examples, 2, i * 2 + 2)
    
    plt.axis('off')
    plt.imshow(imgs[0])

    x1, y1, x2, y2 = coordinates[0]
    x1 = x1 * dataset.img_size[1]
    y1 = y1 * dataset.img_size[0]
    x2 = x2 * dataset.img_size[1]
    y2 = y2 * dataset.img_size[0]

    rect = patches.Rectangle((x1,y1),x2-x1+1,y2-y1+1,linewidth=1,edgecolor='r',facecolor='none')
    plt.gca().add_patch(rect)
    

    if i >= see_examples - 1:
      break
plt.show()


In [4]:
# categories = dataset_train.coco.loadCats(dataset_train.coco.getCatIds())
category2id = dataset.annotations_to_id
id2category = dataset.id_to_annotations
print(category2id)
print(id2category)

{'i8': 0, 'ip': 1, 'i4': 2, 'i14': 3, 'i11': 4, 'i9': 5, 'i15': 6, 'i1': 7, 'i12': 8, 'i10': 9, 'i13': 10, 'il50': 11, 'i6': 12, 'i2': 13, 'i7': 14, 'i5': 15, 'i3': 16}
{0: 'i8', 1: 'ip', 2: 'i4', 3: 'i14', 4: 'i11', 5: 'i9', 6: 'i15', 7: 'i1', 8: 'i12', 9: 'i10', 10: 'i13', 11: 'il50', 12: 'i6', 13: 'i2', 14: 'i7', 15: 'i5', 16: 'i3'}


In [5]:
from transformers import ViTForImageClassification, ViTConfig, ViTModel

# vit_config = ViTConfig(hidden_dropout_prob=0.5, attention_probs_dropout_prob=0.5)

# vit_model = ViTForImageClassification.from_pretrained('google/vit-base-patch16-224-in21k',
#                                                       num_labels=len(category2id),
#                                                       id2label=id2category,
#                                                       label2id=category2id)
vit_backbone_image = ViTModel.from_pretrained('google/vit-base-patch16-384')
# vit_backbone_template = ViTModel.from_pretrained('google/vit-base-patch16-384')

for param in vit_backbone_image.embeddings.parameters():
    param.requires_grad = False
for layer in vit_backbone_image.encoder.layer[:NUM_LAYERS_FROZEN]:
    print(layer)
    for param in layer.parameters():
        param.requires_grad = False
        
# for param in vit_backbone_template.embeddings.parameters():
#     param.requires_grad = False
# for layer in vit_backbone_template.encoder.layer[:NUM_LAYERS_FROZEN]:
#     print(layer)
#     for param in layer.parameters():
#         param.requires_grad = False

# print(vit_model)
# print(vars(vit_backbone))

class SiameseTransformerViT(nn.Module):
    def __init__(self, backbone_image):
        super(SiameseTransformerViT, self).__init__()
        self.backbone_image = backbone_image
        # self.backbone_template = backbone_template
    
        self.bounding_box = nn.Sequential(
            nn.Linear(backbone_image.config.hidden_size * 2, 512),
            nn.ReLU(),
            nn.Dropout(0.2),
            nn.Linear(512, 4),
        )
    def forward_once(self, x):
        x = self.backbone_image(x)
        x = x.last_hidden_state[:, 0, :]
        return x
        

    def forward(self, image, template):
        image_features = self.forward_once(image)
        template_features = self.forward_once(template)
        similarity = nn.functional.cosine_similarity(image_features, template_features)
        bbox_prediction = self.bounding_box(torch.cat([image_features, template_features], 1))
        # features = features.last_hidden_state[:, 0, :]
        # print(features[:, 0, :].shape)
        return image_features, template_features, similarity, bbox_prediction

vit_model = SiameseTransformerViT(vit_backbone_image)


Some weights of the model checkpoint at google/vit-base-patch16-224 were not used when initializing ViTModel: ['classifier.weight', 'classifier.bias']
- This IS expected if you are initializing ViTModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing ViTModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of ViTModel were not initialized from the model checkpoint at google/vit-base-patch16-224 and are newly initialized: ['vit.pooler.dense.bias', 'vit.pooler.dense.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


ViTLayer(
  (attention): ViTAttention(
    (attention): ViTSelfAttention(
      (query): Linear(in_features=768, out_features=768, bias=True)
      (key): Linear(in_features=768, out_features=768, bias=True)
      (value): Linear(in_features=768, out_features=768, bias=True)
      (dropout): Dropout(p=0.0, inplace=False)
    )
    (output): ViTSelfOutput(
      (dense): Linear(in_features=768, out_features=768, bias=True)
      (dropout): Dropout(p=0.0, inplace=False)
    )
  )
  (intermediate): ViTIntermediate(
    (dense): Linear(in_features=768, out_features=3072, bias=True)
    (intermediate_act_fn): GELUActivation()
  )
  (output): ViTOutput(
    (dense): Linear(in_features=3072, out_features=768, bias=True)
    (dropout): Dropout(p=0.0, inplace=False)
  )
  (layernorm_before): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
  (layernorm_after): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
)
ViTLayer(
  (attention): ViTAttention(
    (attention): ViTSelfAttention(
 

In [6]:
def calculate_iou_acc(iou_list, counter):
    iou_list_50 = (iou_list > 0.5).sum()
    iou_list_75 = (iou_list > 0.75).sum()
    iou_list_90 = (iou_list > 0.90).sum()
    return [iou_list_50 / counter, iou_list_75 / counter, iou_list_90 / counter]

def bb_intersection_over_union(boxA, boxB):
    xA = max(boxA[0], boxB[0])
    yA = max(boxA[1], boxB[1])
    xB = min(boxA[2], boxB[2])
    yB = min(boxA[3], boxB[3])
    interArea = max(0, xB - xA + 1) * max(0, yB - yA + 1)
    boxAArea = (boxA[2] - boxA[0] + 1) * (boxA[3] - boxA[1] + 1)
    boxBArea = (boxB[2] - boxB[0] + 1) * (boxB[3] - boxB[1] + 1)
    iou = interArea / float(boxAArea + boxBArea - interArea)
    return iou

def train_epoch(model, train_dataloader, loss_bounding_box, optimizer, device):
    model.train()
    epoch_loss = 0.0
    num_batches = len(train_dataloader)
    predictions = []
    IOU_list = []
    labels = []
    images = []
    templates = []
    for idx, batch in tqdm(enumerate(train_dataloader)):
        batch_images, batch_templates, batch_similarities, batch_bboxs = batch
        batch_images = batch_images.to(device)
        batch_templates = batch_templates.to(device)
        # batch_similarities = batch_similarities.to(device)
        batch_bboxs = batch_bboxs.to(device)

        image_features, template_features, predicted_similarities, predicted_bboxs = model(batch_images, batch_templates)
        
        loss = loss_bounding_box(predicted_bboxs, batch_bboxs)

        loss_scalar = loss.item()

        # if idx % 150 == 0:
        #     print(epoch_acc/(idx + 1))
        #     print(batch_predictions)

        torch.nn.utils.clip_grad_norm_(
            parameters=model.parameters(), max_norm=1.5
        )

        model.zero_grad()
        loss.backward()
        optimizer.step()

        epoch_loss += loss_scalar
        
        bbox_pred = predicted_bboxs.detach().cpu().numpy()
        bbox_original = batch_bboxs.cpu().numpy()

        images.append(batch_images[0].cpu())
        templates.append(batch_templates[0].cpu())
        labels.append(bbox_original[0])
        predictions.append(bbox_pred[0])
        IOU_list.append(bb_intersection_over_union(bbox_pred[0], bbox_original[0]))

    all_data = {
        'images': images,
        'templates': templates,
        'labels': labels,
        'predictions': predictions
    }
    epoch_loss = epoch_loss/num_batches
    IOU_list = np.array(IOU_list)

    return epoch_loss, IOU_list, labels, predictions, all_data


def eval_epoch(model, val_dataloader, loss_bounding_box, device):
    model.eval()
    epoch_loss = 0.0
    num_batches = len(val_dataloader)
    IOU_list = []
    predictions = []
    images = []
    templates = []
    labels = []
    with torch.no_grad():
        for idx, batch in tqdm(enumerate(val_dataloader)):
            batch_images, batch_templates, batch_similarities, batch_bboxs = batch
            batch_images = batch_images.to(device)
            batch_templates = batch_templates.to(device)
            # batch_similarities = batch_similarities.to(device)
            batch_bboxs = batch_bboxs.to(device)

            image_features, template_features, predicted_similarities, predicted_bboxs = model(batch_images, batch_templates)

            loss = loss_bounding_box(predicted_bboxs, batch_bboxs)

            loss_scalar = loss.item()

            epoch_loss += loss_scalar

            bbox_pred = predicted_bboxs.detach().cpu().numpy()
            bbox_original = batch_bboxs.cpu().numpy()
            images.append(batch_images[0].cpu())
            templates.append(batch_templates[0].cpu())
            labels.append(bbox_original[0])
            predictions.append(bbox_pred[0])

            IOU_list.append(bb_intersection_over_union(bbox_pred[0], bbox_original[0]))

        epoch_loss = epoch_loss/num_batches
        IOU_list = np.array(IOU_list)
        all_data = {
            'images': images,
            'templates': templates,
            'labels': labels,
            'predictions': predictions
        }

    return epoch_loss, IOU_list, labels, predictions, all_data



In [ ]:
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
print(device)

# move the model to GPU (when available)
vit_model.to(device)

# create a SGD optimizer
optimizer = torch.optim.AdamW(vit_model.parameters(), lr=lr)
# optimizer = torch.optim.SGD(vit_model.parameters(), lr=1e-3, momentum=0.9)
# optimizer = torch.optim.Adam(vit_model.parameters(), lr=2e-5)

# scheduler = torch.optim.lr_scheduler.ReduceLROnPlateau(optimizer, 'min', patience=1, threshold=1e-2, verbose=True)
# optimizer = torch.optim.AdamW(model.parameters(), lr=0.01)
#
scheduler = torch.optim.lr_scheduler.ReduceLROnPlateau(optimizer, 'min', patience=1, threshold=1e-3, verbose=True)

# set up loss function
loss_criterion = nn.MSELoss()

train_losses = []
train_accuracies = []
train_iou = []
val_losses = []
val_accuracies = []
val_iou =[]
for epoch in range(1, EPOCHS+1):
    train_loss, train_IOU_data, train_bboxes, train_predicted_bboxes, train_all_data = train_epoch(vit_model, train_dataloader, loss_criterion, optimizer, device)
    val_loss, val_IOU_data, val_bboxes, val_predicted_bboxes, val_all_data = eval_epoch(vit_model, valid_dataloader, loss_criterion, device)
    train_IOU_data = calculate_iou_acc(train_IOU_data, len(train_dataloader))
    val_IOU_data = calculate_iou_acc(val_IOU_data, len(valid_dataloader))
    train_losses.append(train_loss)
    val_losses.append(val_loss)
    # train_accuracies.append(train_accuracy)
    # val_accuracies.append(val_accuracy)
    train_iou.append(train_IOU_data)
    val_iou.append(val_IOU_data)
    print('\nEpoch %d'%(epoch))
    print('train loss: %10.8f'%(train_loss))
    print(f"train IOU 50% accuracy: {train_IOU_data[0]}")
    print(f"train IOU 75% accuracy: {train_IOU_data[1]}")
    print(f"train IOU 90% accuracy: {train_IOU_data[2]}")
    print('val loss: %10.8f'%(val_loss))
    print(f"val IOU 50% accuracy: {val_IOU_data[0]}")
    print(f"val IOU 75% accuracy: {val_IOU_data[1]}")
    print(f"val IOU 90% accuracy: {val_IOU_data[2]}")


cuda


200it [00:56,  3.54it/s]
300it [00:14, 21.14it/s]


Epoch 1
train loss: 0.04725004
train IOU 50% accuracy: 0.655
train IOU 75% accuracy: 0.2
train IOU 90% accuracy: 0.01
val loss: 0.03525723
val IOU 50% accuracy: 0.7366666666666667
val IOU 75% accuracy: 0.21333333333333335
val IOU 90% accuracy: 0.016666666666666666



200it [00:55,  3.61it/s]
300it [00:14, 21.20it/s]


Epoch 2
train loss: 0.03217199
train IOU 50% accuracy: 0.77
train IOU 75% accuracy: 0.235
train IOU 90% accuracy: 0.015
val loss: 0.03109638
val IOU 50% accuracy: 0.7666666666666667
val IOU 75% accuracy: 0.37666666666666665
val IOU 90% accuracy: 0.06



73it [00:20,  3.60it/s]

In [15]:
# current_model_path = 'simple_model_base_' + str(NUM_LAYERS_FROZEN) + '_' + str(EPOCHS)
# save_path = os.path.join(data_saved_path, current_model_path)
# try:
#     os.makedirs(save_path)
# except:
#     print("Directory already exists")


In [16]:
# save model
# torch.save(vit_model.state_dict(), os.path.join(save_path, "base_model_weights.pt"))


In [ ]:
# train plots
epoch_list = np.arange(1, EPOCHS + 1, 1)
fig, axs = plt.subplots(1, 2, figsize=(10,5))
axs[0].plot(epoch_list, train_losses)
axs[0].set_title('Train loss')
axs[0].set_xlabel('epochs')
axs[0].set_ylabel('loss')
axs[1].plot(epoch_list, val_losses)
axs[1].set_title('Validation loss')
axs[1].set_xlabel('epochs')
axs[1].set_ylabel('loss')
plt.subplots_adjust(wspace=0.2)
plt.savefig(os.path.join(data_saved_path, 'loss_plots.png'))
plt.show()

train_iou = np.array(train_iou)
fig, axs = plt.subplots(1, 3, figsize=(15,5))
axs[0].plot(epoch_list, train_iou[:, 0])
axs[0].set_title('Train iou 50%')
axs[0].set_xlabel('epochs')
axs[0].set_ylabel('accuracy')
axs[1].plot(epoch_list, train_iou[:, 1])
axs[1].set_title('Train iou 75%')
axs[1].set_xlabel('epochs')
axs[1].set_ylabel('accuracy')
axs[2].plot(epoch_list, train_iou[:, 2])
axs[2].set_title('Train iou 90%')
axs[2].set_xlabel('epochs')
axs[2].set_ylabel('accuracy')
plt.subplots_adjust(wspace=0.3)
plt.savefig(os.path.join(data_saved_path, 'train_iou.png'))
plt.show()

val_iou = np.array(val_iou)
fig, axs = plt.subplots(1, 3, figsize=(15,5))
axs[0].plot(epoch_list, val_iou[:, 0])
axs[0].set_title('Validation iou 50%')
axs[0].set_xlabel('epochs')
axs[0].set_ylabel('accuracy')
axs[1].plot(epoch_list, val_iou[:, 1])
axs[1].set_title('Validation iou 75%')
axs[1].set_xlabel('epochs')
axs[1].set_ylabel('accuracy')
axs[2].plot(epoch_list, val_iou[:, 2])
axs[2].set_title('Validation iou 90%')
axs[2].set_xlabel('epochs')
axs[2].set_ylabel('accuracy')
plt.subplots_adjust(wspace=0.3)
plt.savefig(os.path.join(data_saved_path, 'validation_iou.png'))
plt.show()



In [ ]:
def plot_random_samples(images, templates, labels, predictions, image_size=(224,224), number_samples=5, name='train_results.png'):
    fig = plt.figure(figsize=(20, 7*see_examples))
    for i in range(number_samples):
        index = np.random.randint(len(labels))
        img = images[index].cpu()
        temp = templates[index].cpu()
        label = labels[index]
        prediction = predictions[index]
        # clear_output(wait=True)
        img = np.transpose(img, (1, 2, 0))
        temp = np.transpose(temp, (1, 2, 0))
        fig.add_subplot(see_examples, 3, i * 3 + 1)
        plt.title("Template")
        plt.axis('off')
        plt.imshow(temp)


        l_x1, l_y1, l_x2, l_y2 = label
        l_x1 = l_x1 * image_size[1]
        l_y1 = l_y1 * image_size[0]
        l_x2 = l_x2 * image_size[1]
        l_y2 = l_y2 * image_size[0]

        x1, y1, x2, y2 = prediction
        x1 = x1 * image_size[1]
        y1 = y1 * image_size[0]
        x2 = x2 * image_size[1]
        y2 = y2 * image_size[0]

        fig.add_subplot(see_examples, 3, i * 3 + 2)
        plt.axis('off')
        plt.title(f'xmin={l_x1} ymin={l_y1}\nxmax={l_x2} ymax={l_y2}')
        # plt.title(label)
        plt.imshow(img)
        rect = patches.Rectangle((l_x1,l_y1),l_x2-l_x1+1,l_y2-l_y1+1,linewidth=1,edgecolor='r',facecolor='none')
        plt.gca().add_patch(rect)

        fig.add_subplot(see_examples, 3, i * 3 + 3)
        plt.axis('off')
        plt.title(f'xmin={x1} ymin={y1}\nxmax={x2} ymax={y2}')
        plt.imshow(img)
        rect = patches.Rectangle((x1,y1),x2-x1+1,y2-y1+1,linewidth=1,edgecolor='r',facecolor='none')
        plt.gca().add_patch(rect)

    plt.savefig(os.path.join(data_saved_path, name))
    plt.show()


In [13]:
plot_random_samples(train_all_data['images'], train_all_data['templates'], train_all_data['labels'], train_all_data['predictions'])


In [12]:
plot_random_samples(val_all_data['images'], val_all_data['templates'], val_all_data['labels'], val_all_data['predictions'], name='validation_results.png')


In [11]:
data_dataframe = pd.DataFrame({
    'epochs': epoch_list,
    'train_loss': train_losses,
    'train_iou_50%': train_iou[:, 0],
    'train_iou_75%': train_iou[:, 1],
    'train_iou_90%': train_iou[:, 2],
    'val_loss': val_losses,
    'val_iou_50%': val_iou[:, 0],
    'val_iou_75%': val_iou[:, 1],
    'val_iou_90%': val_iou[:, 2]
})
data_dataframe.to_csv(os.path.join(data_saved_path, "training_data.csv"))
